In [241]:
import app

In [242]:
import pandas as pd
from youtube_transcript_api import YouTubeTranscriptApi
import time
import spacy
import json
from pysbd.utils import PySBDFactory
import pysbd
import altair as alt
import splitter
import enchant
from itertools import chain
import more_itertools

In [2]:
dir(app)

['PySBDFactory',
 'YouTubeTranscriptApi',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__spec__',
 'alt',
 'chain',
 'collapse',
 'convert',
 'convert_df',
 'enchant',
 'flatten',
 'get_sentances',
 'get_subs',
 'json',
 'main',
 'more_itertools',
 'pd',
 'plotbar',
 'posdic',
 'pysbd',
 'pysbd_sentence_boundaries',
 'select_pos',
 'spacy',
 'splitter',
 'st',
 'time',
 'translate']

In [18]:
def main():
    link = "https://www.youtube.com/watch?v=Up5VhPD2xZc"
    link = link.split('v=')[-1]
    data = get_subs(link)
    #with open ('demo.txt','r') as f:
    #    data = f.read()

    #data = json.loads(data)
    text = convert(data)
    #for t in text:
    #    try:
    #        splitter.split(t)

    text = ''.join(map(str,text))

    nlp = spacy.load("en_core_web_sm")
    doc = nlp(text)
    spellcheck = enchant.Dict("en_US")
    clean = ""
    for token in doc:
        if not spellcheck.check(token.text):
            try:
                splitwords = splitter.split(token.text)
                splitwords = ' '.join(map(str,splitwords))
                #st.write(splitwords)
                clean = " ".join([clean, splitwords])
                #st.write(splitwords, "these are split words")
            except:
                pass
                #st.write(longwords, "these are long words")
        else:
            clean = " ".join([clean, token.text])
    return clean

In [19]:
clean = main()

In [22]:
nlp = spacy.load("en_core_web_sm")
doc = nlp(clean)

In [24]:
pos = [(token.text, token.pos_) for token in doc]
df = pd.DataFrame(pos, columns = ['word','pos'])

In [26]:
values = ['PUNCT', 'NUM', 'X', 'SYM']
df = df[df.pos.isin(values) == False]
df = df.groupby('pos')['word'].value_counts().reset_index(level=0)
df['base_word'] = df.index
df = df.reset_index(drop=True)
df = df.rename({'word':'mentions'}, axis=1)

In [36]:
adj = df[df.pos == 'ADJ']

In [38]:
source = df

alt.Chart(adj).mark_bar().encode(
    alt.X("mentions", bin=True),
    y='count()',
)

alt.Chart(...)

In [ ]:
alt.Chart(source).mark_bar().encode(
    x='sum(yield):Q',
    y=alt.Y('site:N', sort='-x')
)

In [49]:
pos = df.groupby('pos')['base_word'].nunique().reset_index()

In [50]:
#Unique words
alt.Chart(source).mark_bar().encode(
    x='mentions',
    y='pos'
)

alt.Chart(...)

In [47]:
df.groupby('pos')['base_word','mentions'].sum().reset_index()

/tmp/ipykernel_44246/1996577194.py:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  df.groupby('pos')['base_word','mentions'].sum().reset_index()


pos  mentions
0     ADJ        81
1     ADP       113
2     ADV       163
3     AUX        65
4   CCONJ        60
5     DET       121
6    INTJ        26
7    NOUN       203
8    PART        27
9    PRON       157
10  PROPN        20
11  SCONJ        41
12  SPACE        46
13   VERB       146

In [43]:
for p in list(['VERB','ADJ','NOUN']):
    print(df[df.pos == str(p)])

    

      pos  mentions  base_word
378  VERB        11         go
379  VERB         9       know
380  VERB         7        see
381  VERB         4        get
382  VERB         3         do
..    ...       ...        ...
472  VERB         1     walked
473  VERB         1   watching
474  VERB         1       went
475  VERB         1       were
476  VERB         1  wondering

[99 rows x 3 columns]
    pos  mentions   base_word
0   ADJ         6      little
1   ADJ         4         big
2   ADJ         4        next
3   ADJ         3        cool
4   ADJ         3        more
5   ADJ         3        most
6   ADJ         2        cold
7   ADJ         2         few
8   ADJ         2      frozen
9   ADJ         2        last
10  ADJ         2       small
11  ADJ         2        sure
12  ADJ         2       windy
13  ADJ         1      actual
14  ADJ         1       alive
15  ADJ         1        anew
16  ADJ         1      arctic
17  ADJ         1      bigger
18  ADJ         1     careful
19  A

In [9]:
def get_subs(link):
    data = app.YouTubeTranscriptApi.get_transcript(link)
    return data

In [11]:
def convert(data):
    j = json.dumps(data)
    j = json.loads(j)
    counter = 0
    subs = []
    for i in j:
        counter += 1
        #start timestamp
        start = time.strftime('%H:%M:%S', time.gmtime(float(i['start'])))
        #end timestamp
        end = start + time.strftime('%H:%M:%S', time.gmtime(float(i['duration'])))

        #subtitle text
        #s = f"{counter}\n{start} --> {end}\n{i['text']}\n"
        #subs.append(s)

        subs.append(i['text'])

    return subs

In [54]:
l =["Inform",
"Confirm ",
" Violate ",
"Consume ",
"Disclose ",
"Interfere ",
"Purity  ",
"Expand  ",
"Duplicate", 
"Preserve",
"Compete ",
"Compromise", 
"Overstate ",
"Prohibit ",
"Restore ",
"Resist ",
"Confess ",
"Debate  ",
"Obey ",
"Encourage", 
"observe",
"Commit",
"Deny",
"Admit",
"Claim",
"Disturb",
"Possess",
"Invest",
"Destroy",
"Accomplish",
"Mess up",
"Maintain",
"Nourish",
"Plant",
"Betray",
"Resign",
"Retreat",
"Insert",
"Tease",
"Swap",
"Stock",
"Face",
"Sink",
"Complete",
"Exhibit",
"Hi",
"jack",
"Strum",
"Reflect",
"Compose",
"Integrate",
"Terminate",
"Litigate",
"Fumble",
"Depend",
"Withdraw"]

In [55]:
type(l)

list

In [243]:
df_level = pd.read_csv("cambridge_britisheng.csv")
df_level = df_level.sort_values(by='level',ascending=True)
df_level = df_level.drop_duplicates(subset=['base_word'], keep='first')

In [253]:
df_level = df_level.rename(columns={"none": "pos"})

In [259]:
df_level.groupby(['level','pos'])['base_word'].count()

level  pos         
A1     adjective        73
       adverb           32
       determiner       25
       exclamation      14
       modal verb        3
       noun            296
       phrasal verb      4
       phrase           54
       preposition      20
       pronoun          16
       verb             81
A2     adjective       131
       adverb           57
       determiner        2
       exclamation       6
       modal verb        6
       noun            536
       phrasal verb     24
       phrase          165
       preposition      18
       pronoun          22
       verb             94
B1     adjective       293
       adverb           85
       determiner        1
       exclamation       2
       modal verb        2
       noun            793
       phrasal verb    119
       phrase          342
       preposition      11
       pronoun           5
       verb            221
B2     adjective       435
       adverb          172
       determiner        1
       n

In [311]:
pd.set_option('display.max_rows', None)
words = df_level[df_level.pos != 'phrase']
words[words.level.isin(['A1','A2','B1','B2'])]

Unnamed: 0                                         base_word  \
7847         7847                                             paint   
10401       10401                                             visit   
10430       10430                                        understand   
10431       10431                                              work   
10432       10432                                             write   
1777         1777                                               dad   
10453       10453                                               yes   
10383       10383                                         Wednesday   
10538       10538                                              well   
10546       10546                                             white   
10547       10547                                            yellow   
10565       10565                                              warm   
10575       10575                                             young   
1684         1684                                              best   
1683         1683                                              a.m.   
1682         1682                                            always   
10541       10541                                              very   
10382       10382                                                TV   
10315       10315                                              year   
10314       10314                                           weekend   
10204       10204                                              wash   
10217       10217                                              walk   
10218       10218                                             watch   
10224       10224                                             woman   
10236       10236                                              want   
10239       10239                                              wife   
10250       10250                                           website   
1853         1853                                      conversation   
10277       10277                                              wine   
10289       10289                                            waiter   
10311       10311                                          waitress   
10312       10312                                              week   
1833         1833                                          computer   
1681         1681                                              also   
10203       10203                                               use   
1680         1680                                             again   
10725       10725                                             wrong   
10856       10856                                               can   
10857       10857                                           between   
10860       10860                                                 a   
10864       10864                                               all   
10865       10865                                                an   
10878       10878                                            cannot   
10883       10883                                             after   
10884       10884                                                at   
10887       10887                                            before   
10866       10866                                              both   
10836       10836                                            behind   
1622         1622                                         all right   
1623         1623                                             cheap   
10778       10778                                                up   
10780       10780                                              when   
10781       10781                                             where   
10782       10782                                               why   
10783       10783                                         yesterday   
10817       10817              

In [308]:
len(wor

7263

In [295]:
pd.set_option('display.max_rows', None)
#table of phrases.
df_level[df_level.pos == 'phrase'].groupby('level').nunique()

Unnamed: 0  base_word  guide_word  pos  category  details  link
level                                                                 
A1             54         54           1    1        12        1    46
A2            165        165           3    1        16        1   145
B1            342        342           1    1        15        1   232
B2            590        590           1    1        17        1   409
C1            424        424           1    1        12        1   318
C2            921        921           2    1        16        1   577

In [304]:
df_level[df_level.pos == 'phrase']

Unnamed: 0                                          base_word  \
11504       11504                                            as well   
11553       11553                 there is/there are/there was, etc.   
11689       11689                       I am Spanish/a teacher, etc.   
11690       11690                                      be called sth   
12911       12911                                        go shopping   
12924       12924                  get here/there/home/to work, etc.   
12925       12925                         get a bus/train/taxi, etc.   
13008       13008                      half past one/two/three, etc.   
13331       13331                                     (Good) morning   
11975       11975                                        for example   
11979       11979                                          Excuse me   
12137       12137                                          of course   
12195       12195                      do the cleaning/cooking, etc.   
12225       12225                                   what does sb do?   
12734       12734                                       good for you   
12749       12749                                      (that's) fine   
12751       12751                                    Don't forget...   
12752       12752                      Happy Birthday/New Year, etc.   
12753       12753                                       How are you?   
13435       13435                                     in the morning   
13454       13454                                     need to do sth   
15557       15557                     not very good/tall/happy, etc.   
13704       13704                           would like sth/to do sth   
14326       14326                                          the radio   
14345       14345                                        Yes, please   
14346       14346                                            see you   
14347       14347                  see you later/soon/tomorrow, etc.   
14366       14366                                           the same   
14375       14375                             it rains/it is raining   
15123       15123                             There is/are/was, etc.   
15124       15124                                             things   
14946       14946                          too small/hard/much, etc.   
13799       13799                        one/two/three, etc. o'clock   
15514       15514                                   be ... years old   
13628       13628                                          very much   
14757       14757                                             Street   
15456       15456                                         Well done!   
15457       15457                            Don't worry (about sth)   
15459       15459                                Would you like ...?   
14532       14532                                        the present   
13539       13539                                      see you later   
13554       13554                                 Would you like...?   
13555       13555                                           how many   
14906       14906                                       see you soon   
13795       13795                        last week/year/Monday, etc.   
13796       13796                                         last night   
13797       13797              more beautiful/difficult/easily, etc.   
13798       13798                        next week/year/Monday, etc.   
14732       14732                        take a picture/photo(graph)   
13650       13650                                   live in/at, etc.   
13626       13626                                         a lot/lots   
14190       14190                           put sth down/in/on, etc.   
14251       14251                                               Road   
13627       13627                                              a lot   
14891       14891                           hav

In [285]:
q = df_level.base_word.value_counts().reset_index()
q[q.base_word > 1]

Empty DataFrame
Columns: [index, base_word]
Index: []

In [288]:
len(df_level)

9759

In [287]:
len(df_level.base_word.unique())

9759

In [274]:
q[q.pos >= 1]

base_word  pos
pos                              
phrase        (Good) morning    1
phrase  (I'll) tell you what    1
phrase          (all) in one    1
phrase     (all) on your own    1
phrase       (all) to myself    1
...                      ...  ...
noun                   youth    1
noun                   zebra    1
noun                     zip    1
noun                    zone    1
noun                     zoo    1

[9700 rows x 2 columns]

In [111]:
z = df_level[['base_word','level','none']]

In [115]:
z.columns = ['base_word','level','pos']

In [121]:
z.groupby('level')['pos'].value_counts()

level  pos         
A1     noun            296
       verb             81
       adjective        73
       phrase           54
       adverb           32
       determiner       25
       preposition      20
       pronoun          16
       exclamation      14
       phrasal verb      4
       modal verb        3
A2     noun            536
       phrase          165
       adjective       131
       verb             94
       adverb           57
       phrasal verb     24
       pronoun          22
       preposition      18
       exclamation       6
       modal verb        6
       determiner        2
B1     noun            793
       phrase          342
       adjective       293
       verb            221
       phrasal verb    119
       adverb           85
       preposition      11
       pronoun           5
       exclamation       2
       modal verb        2
       determiner        1
B2     noun            850
       phrase          590
       adjective       435
       v

In [57]:
df_level = df_level[['base_word','level']]
df_level['level'] = df_level['level'].str.replace('<NA>', '-', regex=False)

In [59]:
len(df_level)

9759

In [65]:
x = df.mask(df_level.base_word.isin(l))

In [66]:
x.base_word.nunique()

289

In [74]:
l = [i.lower().strip() for i in l]

In [80]:
len(df_level.filter(l))

9759

In [240]:
df_level

Unnamed: 0                   base_word    guide_word level  \
7847         7847                       paint  MAKE PICTURE    A1   
8089         8089                        poor      NO MONEY    A1   
8102         8102                         sad           NaN    A1   
8188         8188                    possible    CAN HAPPEN    A1   
8296         8296                       quick          FAST    A1   
...           ...                         ...           ...   ...   
15121       15121    tip sb off or tip off sb           NaN    C2   
15122       15122  top sth off or top off sth           NaN    C2   
200           200                cheerfulness           NaN    C2   
14039       14039             be no mean feat           NaN    C2   
10615       10615               unconditional           NaN    C2   

               none             category  details  \
7847           verb                  NaN  Details   
8089      adjective                money  Details   
8102      adjective  people: personality  Details   
8188      adjective                  NaN  Details   
8296      adjective                  NaN  Details   
...             ...                  ...      ...   
15121  phrasal verb                  NaN  Details   
15122  phrasal verb                  NaN  Details   
200            noun  people: personality  Details   
14039        phrase                  NaN  Details   
10615     adjective                  NaN  Details   

                                     link  
7847   /british-english/words/detail/4099  
8089   /british-english/words/detail/4347  
8102   /british-english/words/detail/5046  
8188   /british-english/words/detail/4370  
8296   /british-english/words/detail/4629  
...                                   ...  
15121  /british-english/words/detail/6060  
15122  /british-english/words/detail/6095  
200     /british-english/words/detail/887  
14039  /british-english/words/detail/3553  
10615  /british-english/words/detail/6261  

[9759 rows x 8 columns]

In [83]:
mask = df_level.base_word.isin(l)
x = df_level[mask]

In [84]:
x

base_word level
1952         face    A1
10959          hi    A1
7029        plant    A1
8743         sink    A2
2800     complete    A2
4713       inform    B1
367         admit    B1
2177      destroy    B1
2762      compete    B1
2035      confirm    B1
2022    encourage    B1
2038      confess    B2
2194      disturb    B2
2187         deny    B2
2723       debate    B2
8424     prohibit    B2
2818       commit    B2
7878       resign    B2
377         claim    B2
8990        stock    B2
8680        tease    B2
1783      consume    B2
635        betray    B2
1948      compose    B2
2015   compromise    B2
5510         obey    B2
5488      observe    B2
5487     maintain    B2
3967       invest    B2
7093     preserve    B2
7097      restore    B2
3591    interfere    B2
2964       expand    B2
7133       resist    B2
7292      reflect    B2
4115    integrate    C1
1168   accomplish    C1
10417    withdraw    C1
7422       purity    C1
2618      exhibit    C1
7801      possess    C1
3568       insert    C1
9541         swap    C1
7614      retreat    C2
10061     violate    C2
1794     disclose    C2

In [88]:
df_level.level.value_counts().sort_values()

A1     645
A2    1081
C1    1506
B1    1881
C2    2084
B2    2562
Name: level, dtype: int64

In [104]:
values = ['A1','A2']
mask = df_level.level.isin(values)

In [105]:
y = df_level[mask]

In [106]:
y.base_word.nunique()

1726

In [107]:
df_level.base_word.nunique()

9759

In [198]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service

In [136]:
from selenium.webdriver.common.by import By

In [128]:
import os
os.getcwd()

'/home/dr-robin/Dev/ytstudy'

In [199]:
def startdriver():
    ser = Service('/home/dr-robin/Dev/ytstudy/chromedriver')
    driver = webdriver.Chrome(service=ser)
    driver = driver.get("https://papago.naver.com/")
    return driver

In [204]:
from time import sleep

def translate(eng):

    xpath='//*[@id="txtSource"]'
    input_box = driver.find_element(By.XPATH,xpath)
    if input_box:
        input_box.send_keys(eng)
    else:
        print('inpoutbox not found')
        
    xpath='//*[@id="btnTranslate"]'
    btn_translate = driver.find_element(By.XPATH,xpath)
    if btn_translate:
        btn_translate.click()
    else:
        print('no translate button')
        
    #get translation
    xpath='//*[@id="txtTarget"]/span'
    output = driver.find_element(By.XPATH,xpath)
    
    if output:
        kor = output.text
        link = driver.current_url
    else:
        print('no output')
    input_box.clear()
    sleep(1)
    return [eng, kor, link]

In [203]:
ser = Service('/home/dr-robin/Dev/ytstudy/chromedriver')
driver = webdriver.Chrome(service=ser)
driver.get("https://papago.naver.com/")

In [206]:
translate('paint')

['paint', '페인트', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=paintpaint']

In [207]:
len(words)

1726

In [208]:
results = []
for word in words:
    try:
        result = translate(word)
        results.append(result)
        print(result)
    except Exception as e:
        print(e)
        break


['paint', '페인트를 칠하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=paint']
['poor', '페인트', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=poor']
['sad', '불쌍한.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=sad']
['possible', '슬퍼', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=possible']
['quick', '가능한', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=quick']
['ready', '빨리', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=ready']
['evening', '준비가 되어 있습니다!', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=evening']
['December', '저녁', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=December']
['die', '12월', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=die']
['student', '다음:', 'https://papago.naver.com/?sk=auto&tk=ko&st=student']
['test', '학생입니다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=test']
['factory', '시험', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=factory']
['show', '공장', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=show']
['take', '쇼우', 'https

['key', '11월', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=key']
['grey', '열쇠', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=grey']
['floor', '회색의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=floor']
['favourite', '바닥.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=favourite']
['good', '마음에 드는', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=good']
['happy', '좋아요.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=happy']
['hour', '행복해', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=hour']
['living room', '한 시간', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=living%20room']
['movie', '거실.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=movie']
['newspaper', '영화.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=newspaper']
['holiday', '신문', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=holiday']
['go', '휴무', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=go']
['fly', '가세요', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=fly']
['nose', '날다', 'https:

['Road', "치즈'!", 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=Road']
['adult', "치즈'!", 'https://papago.naver.com/?sk=auto&tk=ko&st=adult']
['bar', '어른의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=bar']
['clothes', '막대로 막다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=clothes']
['box', '옷이요.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=box']
['bread', '권투를 하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=bread']
['a lot', '빵', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=a%20lot']
['book', '많습니다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=book']
['five', '책', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=five']
['four', '다섯개', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=four']
['animal', '네개', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=animal']
['fifteen', '네개', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=fifteen']
['eight', '열다섯', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=eight']
['a lot/lots', '8', 'https://papago.naver.c

['exciting', '연습하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=exciting']
['run', '신 난다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=run']
['parent', '달려.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=parent']
['need to do sth', '친족', 'https://papago.naver.com/?sk=auto&tk=ko&st=need%20to%20do%20sth']
['coffee', '할 필요가 있다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=coffee']
['ask', '커피.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=ask']
['see you', '물어보다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=see%20you']
['July', '나중에 봐요', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=July']
['twelve', '여행에 의하다', 'https://papago.naver.com/?sk=auto&tk=ko&st=twelve']
['film', '12', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=film']
['eye', '영화', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=eye']
['ear', '눈독을 들이다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=ear']
['zoo', '귀', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=zoo']
['wear', '동물원의',

['year', '할 수 있다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=year']
['very', '연도', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=very']
['January', '아주', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=January']
['visit', '1월', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=visit']
['understand', '방문하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=understand']
['work', '이해하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=work']
['write', '일하다.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=write']
['dad', '글을 쓰세요.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=dad']
['yes', '아빠.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=yes']
['TV', '네.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=TV']
['Wednesday', 'TV', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=Wednesday']
['white', '수요일', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=white']
['yellow', '하얀색', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=yellow']
['warm', '노란 색', 'https://pap

...

['roundabout', '어쩌면요.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=roundabout']
['quickly', '에워싸움', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=quickly']
['railway', '얼른.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=railway']
['platform', '철도의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=platform']
['brain', '연단', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=brain']
['petrol station', '뇌', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=petrol%20station']
['path', '주유소', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=path']
['fashion', '경로.', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=fashion']
['exercise', '유행시키다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=exercise']
['a dance/language/riding, etc. school', '운동', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=a%20dance%25%23x2Flanguage%25%23x2Friding%2C%20etc.%20school']
['delay', '무용 학교/언어 학교/어학원 등', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=delay']
['cost', '지연시키다', 'https://papago

['contact', '타이즈', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=contact']
['bat', '연락', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=bat']
['the south', 'bat', 'https://papago.naver.com/?sk=auto&tk=ko&st=the%20south']
['a sheet of paper/glass, etc.', '남쪽', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=a%20sheet%20of%20paper%25%23x2Fglass%2C%20etc.']
['bus station', '종이 한 장/유리 한 장 등', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=bus%20station']
['snack', '버스 정류장', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=snack']
['soft drink', '과자', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=soft%20drink']
['spoon', '청량 음료', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=spoon']
['star', '숟가락으로 뜨다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=star']
['belt', '별', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=belt']
['boot', '허리띠를 매다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=boot']
['cap', '부팅', 'https://papago.naver.com/?sk=auto&tk=ko&st=cap']
['steak', '모

['size', '철자를 말하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=size']
['square', '크기', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=square']
['term', '광장', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=term']
['timetable', '용어', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=timetable']
['slice', '시간표', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=slice']
['fan', '조각을 내라', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=fan']
['album', '팬들', 'https://papago.naver.com/?sk=auto&tk=ko&st=album']
['fact', '앨범', 'https://papago.naver.com/?sk=auto&tk=ko&st=fact']
['engine', '사실', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=engine']
['dream', '엔진', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=dream']
['discount', '꿈', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=discount']
['disco', '할인하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=disco']
['tell sb to do sth', '원반', 'https://papago.naver.com/?sk=auto&tk=ko&st=tell%20sb%20to%20do%20sth']
['plan', '시키다',

['as well as', '없이', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=as%20well%20as']
['fifth', '게다가', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=fifth']
['hockey', '다섯 번째의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=hockey']
['a variety of sth/sb', '하키', 'https://papago.naver.com/?sk=auto&tk=ko&st=a%20variety%20of%20sth%25%23x2Fsb']
['grandparent', '여러 가지[종류]', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=grandparent']
['grandson', '조부모의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=grandson']
['up the road/street, etc.', '손자', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=up%20the%20road%25%23x2Fstreet%2C%20etc.']
['guidebook', '도로 위/길 위 등', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=guidebook']
['goal', '가이드북', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=goal']
['hobby', '골인', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=hobby']
['notice', '취미', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=notice']
['notebook', '공지', 'https://papago.naver

['skiing', '썬더스톰', 'https://papago.naver.com/?sk=auto&tk=ko&st=skiing']
['surfing', '스키', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=surfing']
['swimming', '스키', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=swimming']
['remember to do sth', '수영하기', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=remember%20to%20do%20sth']
['superlative', '잊지 않고 하다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=superlative']
['plan to do sth', '최상급의', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=plan%20to%20do%20sth']
['the past', '할 계획이다', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=the%20past']
['advice', '과거', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=advice']
['part of sth', '조언', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=part%20of%20sth']
['chat', '일부분을 차지', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=chat']
['set', '고양이', 'https://papago.naver.com/?sk=auto&tk=ko&st=set']
['shop assistant', '세트', 'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=shop%20assi

In [234]:
results[98]
for i in range(len(results)):
    kor = i+1
    print(results[i][0], results[kor][1], results[i][2])

1
paint 페인트 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=paint
2
poor 불쌍한. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=poor
3
sad 슬퍼 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=sad
4
possible 가능한 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=possible
5
quick 빨리 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=quick
6
ready 준비가 되어 있습니다! https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=ready
7
evening 저녁 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=evening
8
December 12월 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=December
9
die 다음: https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=die
10
student 학생입니다 https://papago.naver.com/?sk=auto&tk=ko&st=student
11
test 시험 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=test
12
factory 공장 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=factory
13
show 쇼우 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=show
14
take 가지고 가다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=take
15
smoke 담배를 피우다 https://papago.naver.com/?sk=auto&tk=ko&hn

cold 추워요 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=cold
465
any 조금도 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=any
466
an an https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=an
467
cannot 수 없다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=cannot
468
after 끝나고 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=after
469
at 에서 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=at
470
before 전에 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=before
471
both 둘다요. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=both
472
behind 뒤에 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=behind
473
all right 좋아요. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=all%20right
474
cheap 싸다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=cheap
475
up 업. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=up
476
when 언제 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=when
477
where 어디에 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=where
478
why 왜죠 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=why
479
y

roof 지붕을 씌우다 https://papago.naver.com/?sk=auto&tk=ko&st=roof
899
pound 파운드 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=pound
900
try on sth or try sth on 입어보다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=try%20on%20sth%20or%20try%20sth%20on
901
exactly 그렇고말고! https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=exactly
902
spare time 시간이 얼마 남지 않은 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=spare%20time
903
practice 연습하세요. https://papago.naver.com/?sk=auto&tk=ko&st=practice
904
especially 특히. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=especially
905
point 가르키다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=point
906
repair 수리 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=repair
907
electric 전기의 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=electric
908
pull 당기다. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=pull
909
push 밀다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=push
910
perfume Common https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=perfume
911
prefer 선호하다 htt

spelling 맞춤법 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=spelling
1365
I suppose 그렇구나. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=I%20suppose
1366
swimming costume 수영복 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=swimming%20costume
1367
rugby 럭비 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=rugby
1368
tie 쇠붙이 https://papago.naver.com/?sk=auto&tk=ko&st=tie
1369
blood 피를 흘리다 https://papago.naver.com/?sk=auto&tk=ko&st=blood
1370
round 동그랗게 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=round
1371
stage 단계. https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=stage
1372
suit 뒤따라다니다 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=suit
1373
cycling 사이클링의 https://papago.naver.com/?sk=auto&tk=ko&st=cycling
1374
stomach 배 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=stomach
1375
speaker 화자 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=speaker
1376
teenager 십대 https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=teenager
1377
and so on 기타 등등 https://papago.naver.com/?sk=auto&tk=ko&st=a

IndexError: list index out of range

In [236]:
result[-2]

'사촌동생'

In [192]:
s = ' '.join(words)

import string
def find_whitespace(st):
    for index, character in enumerate(st):
        if character in string.whitespace:
            yield index

idx = list(find_whitespace(s))


AttributeError: 'list' object has no attribute 'max'

In [187]:
s

"paint poor sad possible quick ready evening December die student test factory show take smoke start stop subject driver eat really shirt skirt T-shirt trousers talk speak tell red shoe safe right pay phone play remember ride same p.m. think son table toilet tree summer quarter September pig tomato page picture radio pen pencil pet question family photo sister tea doctor sport tennis street taxi shower send town sugar snow end day date dance credit card country soup example tooth sheep smoking hot here how group get hospital Friday hard February great the Internet important interesting hungry funny fine feel mum first hotel life horse March May Monday morning night green November key grey floor favourite good happy hour living room movie newspaper holiday go fly nose jacket jeans language letter mouth message note game in the morning late television email dancing name leg music football friend fun lesson learn knife hair meal girl meat milk juice lunch help hear finish husband kitchen 

'페인트'

In [179]:
driver.current_url

'https://papago.naver.com/?sk=auto&tk=ko&hn=0&st=paint'

In [139]:
words = df_level.base_word.unique()

In [147]:
df_level.sort_values(by='level', inplace=True)

In [159]:
mask = df_level.level.isin(['A1','A2'])
words = df_level[mask].base_word.unique()

In [ ]:
//*[@id="root"]/div/div[1]/section/div/div[2]/div/div[1]/dl[1]